<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:right;border-radius:5px 5px;">
    <i>Aprender una técnica no es un fin en si mismo, simplemente indica por donde hay que empezar</i><br><b>Proverbio Japonés</b></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:right;border-radius:5px 5px;">
<i>Material curado y organizado por el Prof. Dr. Hernán D. Merlino</i><br> 
<i>Retrieval Augmented Generation (RAG)  Versión 2.0 - 2024 Q3</i></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>_____________________________________________________________</strong></p> 

<a id = "1.0"></a>
<p style="font-size:25px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>R</strong>etrieval <strong>A</strong>ugmented <strong>G</strong>eneration</p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Cargar librerías</strong></p> 

In [1]:
import os
BASE_DIR = '../'
PATH_TO_TRAIN = 'grafo_hierarquia_completo.json'

In [2]:
import warnings
warnings.filterwarnings("ignore")

In [3]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

In [4]:
from transformers import pipeline

In [31]:
import pandas as pd
import json

# Cargar el archivo de la jerarquía JSON
with open("grafo_hierarquia_completo.json", "r", encoding="utf-8") as f:
    grafo_json = json.load(f)

def crear_dataframe(datos):
    filas = []
    for cultivo, info_cultivo in datos.items():
        for producto, info_producto in info_cultivo['Productos'].items():
            for plaga, info_plaga in info_producto['Controla a'].items():
                # Obtener el nombre común de la plaga
                nombre_comun_plaga = info_plaga.get('Nombre Comun', 'No disponible')
                
                # Concatenar los detalles de los momentos de aplicación (sin el "Periodo de Carencia")
                momentos_aplicacion = []
                periodos_carencia = []  # Lista para los períodos de carencia
                for momento in info_plaga['Momento de aplicacion']:
                    periodo = momento['Periodo']
                    periodo_carencia = momento['Periodo de Carencia'] if momento['Periodo de Carencia'] else 'No aplica'
                    momentos_aplicacion.append(f"Periodo: {periodo}")
                    periodos_carencia.append(periodo_carencia)
                
                # Obtener la dosificación y unidad de medida
                dosificacion_min = info_producto.get('Dosificacion Min', 'No disponible')
                dosificacion_max = info_producto.get('Dosificacion Max', 'No disponible')
                unidad_medida = info_producto.get('Unidad de Medida', 'No disponible')
                
                # Crear la fila con todos los datos, incluyendo el "Periodo de Carencia"
                fila = {
                    'Cultivo': cultivo,
                    'Producto': producto,
                    'Plaga': plaga,
                    'Nombre Comun Plaga': nombre_comun_plaga,
                    'Dosificacion Min': dosificacion_min,
                    'Dosificacion Max': dosificacion_max,
                    'Unidad de Medida': unidad_medida,
                    'Momentos de aplicación': ' | '.join(momentos_aplicacion),
                    'Periodo de Carencia': ' | '.join(periodos_carencia)
                }
                filas.append(fila)
    
    return pd.DataFrame(filas)

# Crear el DataFrame
df = crear_dataframe(grafo_json)

# Mostrar el DataFrame
print(df.head())

  Cultivo            Producto                    Plaga     Nombre Comun Plaga  \
0    Maíz  7344 VT Triple PRO  Helicoverpa gelotopoeon        Isoca bolillera   
1    Maíz  7344 VT Triple PRO    Spodoptera frugiperda  Oruga militar tardía    
2    Maíz  7349 VT Triple PRO  Helicoverpa gelotopoeon        Isoca bolillera   
3    Maíz  7349 VT Triple PRO    Spodoptera frugiperda  Oruga militar tardía    
4    Maíz             Fastac®  Helicoverpa gelotopoeon        Isoca bolillera   

  Dosificacion Min Dosificacion Max Unidad de Medida  \
0              0.0              0.0             None   
1              0.0              0.0             None   
2    No disponible    No disponible    No disponible   
3    No disponible    No disponible    No disponible   
4    No disponible    No disponible    No disponible   

                              Momentos de aplicación  \
0  Periodo: Aplicar cuando se registren 3-4 Isoca...   
1  Periodo: Aplicar cuando se registren 3-4 Isoca...   
2  Perio

In [56]:
df['Nombre Comun Plaga']

0             isoca bolillera
1       oruga militar tardía 
2             isoca bolillera
3       oruga militar tardía 
4             isoca bolillera
                ...          
2978                pega pega
2979            yerba de sapo
2980               eleocharis
2981                    junco
2982                 roedores
Name: Nombre Comun Plaga, Length: 2983, dtype: object

In [ ]:
df['Nombre Comun Plaga'] = df['Nombre Comun Plaga'].apply(preprocess_query)

In [59]:
# Convertir a minúsculas las columnas correspondientes
df['Producto'] = df['Producto'].str.lower()
df['Plaga'] = df['Plaga'].str.lower()
df['Cultivo'] = df['Cultivo'].str.lower()
df['Momentos de aplicación'] = df['Momentos de aplicación'].str.lower()
df['Nombre Comun Plaga'] = df['Nombre Comun Plaga'].str.lower()  # Nueva columna añadida
df['Periodo de Carencia'] = df['Periodo de Carencia'].str.lower()  # Nueva columna añadida

# Mostrar el DataFrame con las columnas transformadas
print(df.head())

  Cultivo            Producto                    Plaga     Nombre Comun Plaga  \
0    maíz  7344 vt triple pro  helicoverpa gelotopoeon       isocar bolillero   
1    maíz  7344 vt triple pro    spodoptera frugiperda  orugar militar tardir   
2    maíz  7349 vt triple pro  helicoverpa gelotopoeon       isocar bolillero   
3    maíz  7349 vt triple pro    spodoptera frugiperda  orugar militar tardir   
4    maíz             fastac®  helicoverpa gelotopoeon       isocar bolillero   

  Dosificacion Min Dosificacion Max Unidad de Medida  \
0              0.0              0.0             None   
1              0.0              0.0             None   
2    No disponible    No disponible    No disponible   
3    No disponible    No disponible    No disponible   
4    No disponible    No disponible    No disponible   

                              Momentos de aplicación  \
0  periodo: aplicar cuando se registren 3-4 isoca...   
1  periodo: aplicar cuando se registren 3-4 isoca...   
2  perio

In [60]:
# Crear la columna 'texto' con la estructura deseada
df['texto'] = df.apply(lambda row: f"El producto {row['Producto']} combate a la plaga {row['Plaga']} ({row['Nombre Comun Plaga']}) y se usa en el cultivo {row['Cultivo']}. Se debe aplicar en el siguiente momento: {row['Momentos de aplicación']}. El periodo de carencia es: {row['Periodo de Carencia']}.", axis=1)

# Mostrar el DataFrame con la nueva columna 'texto'
print(df[['Producto', 'Plaga', 'Cultivo', 'Momentos de aplicación', 'Periodo de Carencia', 'texto']].head())

             Producto                    Plaga Cultivo  \
0  7344 vt triple pro  helicoverpa gelotopoeon    maíz   
1  7344 vt triple pro    spodoptera frugiperda    maíz   
2  7349 vt triple pro  helicoverpa gelotopoeon    maíz   
3  7349 vt triple pro    spodoptera frugiperda    maíz   
4             fastac®  helicoverpa gelotopoeon    maíz   

                              Momentos de aplicación  \
0  periodo: aplicar cuando se registren 3-4 isoca...   
1  periodo: aplicar cuando se registren 3-4 isoca...   
2  periodo: aplicar cuando se registren 3-4 isoca...   
3  periodo: aplicar cuando se registren 3-4 isoca...   
4  periodo: aplicar cuando se registren 3-4 isoca...   

                                 Periodo de Carencia  \
0                  no aplica | no aplica | no aplica   
1  no aplica | no aplica | no aplica | no aplica ...   
2                  no aplica | no aplica | no aplica   
3  no aplica | no aplica | no aplica | no aplica ...   
4                  no aplica | no 

<p style="font-size:17px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https://huggingface.co/docs/transformers/main_classes/pipelines" target=\"_blank\">Pipelines Method</a></p>

<p style="font-size:17px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https://huggingface.co/docs/transformers/v4.46.0/en/add_new_pipeline" target=\"_blank\">How to create a custom pipeline?</a></p>

In [61]:
documents = [f'"{texto}."' for texto in df['texto']]

In [62]:
documents

['"El producto 7344 vt triple pro combate a la plaga helicoverpa gelotopoeon (isocar bolillero) y se usa en el cultivo maíz. Se debe aplicar en el siguiente momento: periodo: aplicar cuando se registren 3-4 isocas por m². | periodo: iniciar los tratamientos cuando se detecten 3 o 4 isocas por metro lineal de surco. realizar tratamientos terrestres antes de que el cultivo supere los 50 cm de altura, con caudales de 100 litros/ha. | periodo: *adicionar coadyuvante (dash mso max) a razón de 250 cc/ha. aplicar cuando se alcance el umbral de 1 a 2 larvas (l1-l2) /m lineal de surco. estadío del cultivo en estadío vegetativos tempranos. . El periodo de carencia es: no aplica | no aplica | no aplica.."',
 '"El producto 7344 vt triple pro combate a la plaga spodoptera frugiperda (orugar militar tardir) y se usa en el cultivo maíz. Se debe aplicar en el siguiente momento: periodo: aplicar cuando se registren 3-4 isocas por m². | periodo: antes de floración, aplicar al observar 15 isocas por metr

In [88]:
generator = pipeline(task="conversational",model="datificate/gpt2-small-spanish")

KeyError: "Unknown task conversational, available tasks are ['audio-classification', 'automatic-speech-recognition', 'depth-estimation', 'document-question-answering', 'feature-extraction', 'fill-mask', 'image-classification', 'image-feature-extraction', 'image-segmentation', 'image-to-image', 'image-to-text', 'mask-generation', 'ner', 'object-detection', 'question-answering', 'sentiment-analysis', 'summarization', 'table-question-answering', 'text-classification', 'text-generation', 'text-to-audio', 'text-to-speech', 'text2text-generation', 'token-classification', 'translation', 'video-classification', 'visual-question-answering', 'vqa', 'zero-shot-audio-classification', 'zero-shot-classification', 'zero-shot-image-classification', 'zero-shot-object-detection', 'translation_XX_to_YY']"

<p style="font-size:17px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https://huggingface.co/models?pipeline_tag=text-generation&sort=trending&search=spanish" target=\"_blank\">Spanish models</a></p>

<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https:///huggingface.co/datificate/gpt2-small-spanish" target=\"_blank\">GPT2-small-spanish is a state-of-the-art language model for Spanish based on the GPT-2 small model</a></p>

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Corpus de documentos</strong></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Vectorización</strong></p> 

In [65]:
documents

['"El producto 7344 vt triple pro combate a la plaga helicoverpa gelotopoeon (isocar bolillero) y se usa en el cultivo maíz. Se debe aplicar en el siguiente momento: periodo: aplicar cuando se registren 3-4 isocas por m². | periodo: iniciar los tratamientos cuando se detecten 3 o 4 isocas por metro lineal de surco. realizar tratamientos terrestres antes de que el cultivo supere los 50 cm de altura, con caudales de 100 litros/ha. | periodo: *adicionar coadyuvante (dash mso max) a razón de 250 cc/ha. aplicar cuando se alcance el umbral de 1 a 2 larvas (l1-l2) /m lineal de surco. estadío del cultivo en estadío vegetativos tempranos. . El periodo de carencia es: no aplica | no aplica | no aplica.."',
 '"El producto 7344 vt triple pro combate a la plaga spodoptera frugiperda (orugar militar tardir) y se usa en el cultivo maíz. Se debe aplicar en el siguiente momento: periodo: aplicar cuando se registren 3-4 isocas por m². | periodo: antes de floración, aplicar al observar 15 isocas por metr

In [66]:
vectorizer = TfidfVectorizer()
doc_vectors = vectorizer.fit_transform(documents)

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Métodos</strong></p> 

In [67]:
def retrieve_document(query, vectorizer, doc_vectors):
    query_vector = vectorizer.transform([query])
    similarities = cosine_similarity(query_vector, doc_vectors)
    most_similar_idx = similarities.argmax()
    return documents[most_similar_idx]

In [68]:
def rag_example(query):
    document = retrieve_document(query, vectorizer, doc_vectors)
    answer = generator(document,
                       max_length=1024,
                       num_return_sequences=1,
                       temperature=0.95,
                       top_k=50,  
                       top_p=0.9)
    return answer[0]["generated_text"]

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong><u>Params</u></strong>:
<ul style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<li><i><b>document:</b></i> texto base</li>
<li><i><b>max_length:</b></i> genera hasta 50 tokens</li>
<li><i><b>num_return_sequences:</b></i> retorna solo un texto</li>
<li><i><b>temperature:</b></i> ajusta la creatividad del modelo</li>
<li><i><b>top_k y top_p:</b></i> controlan la selección de palabras para una generación más coherente y variada</li>
</ul></p>

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Pregunta</strong></p> 

In [69]:
import spacy
import nltk
from nltk.corpus import stopwords

# Cargar recursos necesarios
nltk.download('stopwords')
stop_words = set(stopwords.words('spanish'))
nlp = spacy.load("es_core_news_sm")

def preprocess_query(query):
    # Tokenizar y analizar la consulta
    doc = nlp(query)
    # Lematización y eliminación de stopwords
    lemmatized_tokens = [
        token.lemma_
        for token in doc
        if token.text.lower() not in stop_words and not token.is_punct
    ]
    return " ".join(lemmatized_tokens)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\cacic\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [81]:
query = "que producto recomienda para el sorgo de alepo en el cultivo de la soja"
query=preprocess_query(query)
print(query)
answer = rag_example(query)

producto recomendar sorgo alepo cultivo soja


In [82]:
answer_cortada = answer.split('.')[0]

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Respuesta</strong></p> 

In [83]:
print(answer_cortada)

"El producto zynion™ combate a la plaga sorghum halepensis (sorgo alepo) y se usa en el cultivo algodón


<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>_____________________________________________________________</strong></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>_____________________________________________________________</strong></p> 